# 1M_recipes dataset word2vec experiments

In [1]:
import numpy as np
import json

import nltk
from nltk.stem import PorterStemmer
from nltk.stem import LancasterStemmer
from nltk.corpus import stopwords as nltk_stopwords

from pprint import pprint

from gensim.test.utils import common_texts, get_tmpfile
from gensim.models import Word2Vec

from json_buffered_reader import JSON_buffered_reader as JSON_br

import settings

In [2]:
from ipypb import track

* reading firs n recipes from json stream

In [3]:
n = 100000

In [4]:
buffered_reader = JSON_br(settings.one_million_recipes_file)

In [5]:
instructions = []

----

In [6]:
stopwords = set(nltk_stopwords.words('english'))
sentence_symbols = set(('.', ';', '!', '?', ',')) 
porter = PorterStemmer()
model = None

stemmed_stopwords = set([porter.stem(word) for word in stopwords])

def recipe2instructions(stream_item):
    return [t['text'] for t in stream_item['instructions']]

def stemmed_recipe_instruction(json_item, stemmer = porter):
    item_instructions = recipe2instructions(json_item)
    stemmed_list = []
    for instruction in item_instructions:
        stemmed_list.append([stemmer.stem(i).lower() for i in nltk.word_tokenize(instruction)])
    
    result = []
    for stemmed in stemmed_list:
        stemmed_without_stopwords = []
        for word in stemmed:
            if (word not in stopwords) and (word not in sentence_symbols):
                stemmed_without_stopwords.append(word)
        result.append(stemmed_without_stopwords)
    
    return  result


* example:

In [7]:
#item = buffered_reader.__next__()

In [8]:
#stemmed_recipe_instruction(item)

* reading up to n recipes:

In [9]:

for i in track(range(n)):
    json_recipe = buffered_reader.__next__()
    instructions += stemmed_recipe_instruction(json_recipe)
    #print(i)


 [████████████████████████████████████████████████████████████] 100000/100000 [06:06<00:00, 0.00s/it]

* train word2vec on that instructions

In [10]:
model = Word2Vec(instructions, size=512, window=1, min_count=3, workers=4)
def word_similarity(word_a:str, word_b:str, model=model, stemmer=porter):
    return model.wv.similarity(stemmer.stem(word_a), stemmer.stem(word_b))

def word_exists(word:str, model=model, stemmer=porter):
    return stemmer.stem(word) in model.wv


In [11]:
word_similarity("dice", "onions")

0.42250293

In [12]:
model.wv.most_similar_to_given("wash", ["salad","potato", "oil", "tomato"])

'salad'

* check for a list of cooking verbs and ingredients whether they're represented by our model

In [13]:
from cooking_vocab import cooking_verbs
from cooking_ingredients import ingredients

In [14]:
model_actions = []
model_ingredients = []

In [15]:
for action in cooking_verbs:
    if word_exists(action):
        model_actions.append(action)

for ingredient in ingredients:
    if word_exists(ingredient):
        model_ingredients.append(ingredient)

In [16]:
pprint(f"found {len(model_actions)} of {len(cooking_verbs)} valid actions and {len(model_ingredients)} of {len(ingredients)} valid ingredients")

'found 108 of 111 valid actions and 160 of 648 valid ingredients'


In [17]:
stemmed_ingredients = [porter.stem(ing) for ing in model_ingredients]
stemmed_actions = [porter.stem(act) for act in model_actions]

## cross-category-similarites
* now get the most likely ingredients for every action:

### Cooking Action to Ingredient

In [18]:
for action in model_actions:
    ings = stemmed_ingredients[:]
    best_ingredients = []
    for i in range(10):
        best = model.wv.most_similar_to_given(porter.stem(action), ings)
        ings.remove(best)
        best_ingredients.append(best)
    print(f"{action} --> {best_ingredients}")

add --> ['scallion', 'celeri', 'parsley', 'onion', 'thyme', 'garlic', 'chive', 'oregano', 'salt', 'cilantro']
adjust --> ['cayenn', 'salt', 'sriracha', 'pepper', 'nutmeg', 'oregano', 'marjoram', 'cumin', 'tumer', 'cornflour']
arrange --> ['scallion', 'lettuc', 'zucchini', 'avocado', 'cucumb', 'arugula', 'pineappl', 'onion', 'carrot', 'watercress']
bake --> ['cornmeal', 'cinnamon', 'pecan', 'flour', 'margarin', 'vanilla', 'butter', 'shorten', 'walnut', 'almond']
baste --> ['veget', 'chicken', 'pork', 'meat', 'juic', 'season', 'kimchi', 'beer', 'honey', 'mirin']
batter --> ['dough', 'flour', 'polenta', 'cornmeal', 'coconut', 'ice', 'pecan', 'grit', 'buttermilk', 'tortilla']
beat --> ['vanilla', 'buttermilk', 'shorten', 'cream', 'milk', 'sugar', 'molass', 'egg', 'margarin', 'mascarpon']
blend --> ['buttermilk', 'honey', 'molass', 'nutmeg', 'cream', 'vanilla', 'allspic', 'milk', 'chickpea', 'cayenn']
boil --> ['water', 'penn', 'dashi', 'cornflour', 'saffron', 'mirin', 'sake', 'spaghetti', 

### Ingredient to Cooking Action

In [19]:
for ingredient in model_ingredients:
    acts = stemmed_actions[:]
    best_actions = []
    for i in range(10):
        best = model.wv.most_similar_to_given(porter.stem(ingredient), acts)
        acts.remove(best)
        best_actions.append(best)
    print(f"{ingredient} --> {best_actions}")

salt --> ['salt', 'add', 'sprinkl', 'season', 'sugar', 'grind', 'rub', 'mix', 'stir', 'tast']
garlic --> ['minc', 'add', 'sprinkl', 'salt', 'stir', 'season', 'chop', 'dice', 'pickl', 'grind']
onions --> ['minc', 'add', 'stir', 'dice', 'chop', 'salt', 'sprinkl', 'arrang', 'pickl', 'parboil']
water --> ['boil', 'add', 'sugar', 'salt', 'flour', 'pour', 'stir', 'soak', 'rins', 'steam']
sugar --> ['sugar', 'beat', 'salt', 'whisk', 'flour', 'add', 'sweeten', 'sprinkl', 'mix', 'stir']
butter --> ['flour', 'sugar', 'melt', 'sprinkl', 'spread', 'add', 'beat', 'put', 'salt', 'brown']
pepper --> ['season', 'salt', 'sprinkl', 'add', 'minc', 'tast', 'pickl', 'spice', 'rub', 'chop']
eggs --> ['beat', 'mix', 'fold', 'add', 'brush', 'flour', 'whisk', 'curdl', 'put', 'place']
tomatoes --> ['add', 'pickl', 'dice', 'stir', 'minc', 'pour', 'arrang', 'squeez', 'garnish', 'put']
carrots --> ['parboil', 'minc', 'dice', 'add', 'peel', 'chop', 'stir', 'slice', 'buri', 'arrang']
milk --> ['beat', 'sour', 'add',

----
## Inter-Category-Similarities
* checking self similarities:

### Cooking Action

In [21]:
for action in model_actions:
    acts = stemmed_actions[:]
    best_actions = []
    for i in range(10):
        best = model.wv.most_similar_to_given(porter.stem(action), acts)
        acts.remove(best)
        best_actions.append(best)
    print(f"{action} --> {best_actions}")

add --> ['add', 'put', 'place', 'pour', 'sprinkl', 'stir', 'arrang', 'mix', 'minc', 'chop']
adjust --> ['adjust', 'correct', 'check', 'reduc', 'tast', 'lower', 'salt', 'simmer', 'thicken', 'blend']
arrange --> ['arrang', 'place', 'put', 'cut', 'spread', 'add', 'sprinkl', 'slice', 'pour', 'fold']
bake --> ['bake', 'roast', 'broil', 'place', 'set', 'put', 'sprinkl', 'flour', 'cook', 'brush']
baste --> ['bast', 'brush', 'brais', 'check', 'marin', 'rub', 'glaze', 'broil', 'grill', 'debon']
batter --> ['batter', 'glaze', 'spread', 'flour', 'spoon', 'pour', 'knead', 'whip', 'scorch', 'cool']
beat --> ['beat', 'whisk', 'mix', 'whip', 'blend', 'sugar', 'stir', 'fold', 'add', 'knead']
blend --> ['blend', 'mix', 'beat', 'stir', 'whisk', 'add', 'chill', 'mash', 'knead', 'grind']
boil --> ['boil', 'simmer', 'cook', 'thicken', 'heat', 'stir', 'parboil', 'cover', 'reduc', 'steam']
braise --> ['brais', 'poach', 'bast', 'roast', 'cook', 'carv', 'debon', 'reduc', 'simmer', 'remov']
break --> ['break', 

### Ingredient

In [22]:
for ingredient in model_ingredients:
    ings = stemmed_ingredients[:]
    best_ingredients = []
    for i in range(10):
        best = model.wv.most_similar_to_given(porter.stem(ingredient), ings)
        ings.remove(best)
        best_ingredients.append(best)
    print(f"{ingredient} --> {best_ingredients}")

salt --> ['salt', 'cayenn', 'nutmeg', 'paprika', 'allspic', 'marjoram', 'oregano', 'cumin', 'thyme', 'cardamom']
garlic --> ['garlic', 'shallot', 'oregano', 'cumin', 'thyme', 'coriand', 'cayenn', 'marjoram', 'tumer', 'scallion']
onions --> ['onion', 'shallot', 'scallion', 'celeri', 'gingerroot', 'leek', 'garlic', 'chili', 'caper', 'chilli']
water --> ['water', 'milk', 'sake', 'juic', 'vinegar', 'oil', 'sugar', 'mirin', 'saffron', 'salt']
sugar --> ['sugar', 'honey', 'molass', 'cinnamon', 'nutmeg', 'allspic', 'margarin', 'cardamom', 'vanilla', 'milk']
butter --> ['butter', 'margarin', 'shorten', 'lard', 'ghee', 'oil', 'cinnamon', 'honey', 'flour', 'sugar']
pepper --> ['pepper', 'peppercorn', 'cumin', 'cayenn', 'oregano', 'paprika', 'garlic', 'chilli', 'chile', 'thyme']
eggs --> ['egg', 'buttermilk', 'molass', 'margarin', 'coconut', 'butter', 'ricotta', 'flour', 'banana', 'milk']
tomatoes --> ['tomato', 'tomatillo', 'pimento', 'avocado', 'caper', 'chile', 'cucumb', 'mango', 'mushroom', '